In [3]:
!pip3 install gym

In [4]:
!git clone https://github.com/openai/gym 

fatal: destination path 'gym' already exists and is not an empty directory.


In [5]:
cd gym

/Users/akshayanagarajan/gym


In [6]:
pip install -e .

Obtaining file:///Users/akshayanagarajan/gym
  Attempting uninstall: gym
    Found existing installation: gym 0.17.3
    Uninstalling gym-0.17.3:
      Successfully uninstalled gym-0.17.3
  Running setup.py develop for gym
Note: you may need to restart the kernel to use updated packages.


In [ ]:
import gym
import numpy as np

#MAX_NUM_EPISODES = 500
MAX_NUM_EPISODES = 50000
STEPS_PER_EPISODE = 200 #  This is specific to MountainCar. May change with env
EPSILON_MIN = 0.005
max_num_steps = MAX_NUM_EPISODES * STEPS_PER_EPISODE
EPSILON_DECAY = 500 * EPSILON_MIN / max_num_steps
ALPHA = 0.05  # Learning rate
GAMMA = 0.98  # Discount factor
NUM_DISCRETE_BINS = 30  # Number of bins to Discretize each observation dim


class Q_Learner(object):
    def __init__(self, env):
        self.obs_shape = env.observation_space.shape
        self.obs_high = env.observation_space.high
        self.obs_low = env.observation_space.low
        self.obs_bins = NUM_DISCRETE_BINS  # Number of bins to Discretize each observation dim
        self.bin_width = (self.obs_high - self.obs_low) / self.obs_bins
        self.action_shape = env.action_space.n
        # Create a multi-dimensional array (aka. Table) to represent the
        # Q-values
        self.Q = np.zeros((self.obs_bins + 1, self.obs_bins + 1,
                           self.action_shape))  # (51 x 51 x 3)
        self.alpha = ALPHA  # Learning rate
        self.gamma = GAMMA  # Discount factor
        self.epsilon = 1.0

    def discretize(self, obs):
        return tuple(((obs - self.obs_low) / self.bin_width).astype(int))

    def get_action(self, obs):
        discretized_obs = self.discretize(obs)
        # Epsilon-Greedy action selection
        if self.epsilon > EPSILON_MIN:
            self.epsilon -= EPSILON_DECAY
        if np.random.random() > self.epsilon:
            return np.argmax(self.Q[discretized_obs])
        else:  # Choose a random action
            return np.random.choice([a for a in range(self.action_shape)])

    def learn(self, obs, action, reward, next_obs):
        discretized_obs = self.discretize(obs)
        discretized_next_obs = self.discretize(next_obs)
        #td_target = reward + self.gamma * np.max(self.Q[discretized_next_obs])
        next_action = agent.get_action(next_obs)
        td_target = reward + self.gamma * self.Q[discretized_next_obs][next_action]
        td_error = td_target - self.Q[discretized_obs][action]
        self.Q[discretized_obs][action] += self.alpha * td_error
        action = next_action

def train(agent, env):
    best_reward = -float('inf')
    for episode in range(MAX_NUM_EPISODES):
        done = False
        obs = env.reset()
        total_reward = 0.0
        action = agent.get_action(obs)      
        while not done:
            next_obs, reward, done, _ = env.step(action) 
            total_reward += reward # abs(obs[0]+0.5)
            agent.learn(obs, action, reward, next_obs)
            obs = next_obs            
        if total_reward > best_reward:
            best_reward = total_reward
        print("Episode#:{} reward:{} best_reward:{} eps:{}".format(episode, total_reward, best_reward, agent.epsilon))
    # Return the trained policy
    return np.argmax(agent.Q, axis=2)


def test(agent, env, policy):
    done = False
    obs = env.reset()
    total_reward = 0.0
    while not done:
        action = policy[agent.discretize(obs)]
        next_obs, reward, done, info = env.step(action)
        obs = next_obs
        total_reward += reward
    return total_reward


if __name__ == "__main__":
    env = gym.make('MountainCar-v0')
    agent = Q_Learner(env)
    learned_policy = train(agent, env)
    # Use the Gym Monitor wrapper to evalaute the agent and record video
    gym_monitor_path = "./gym_monitor_output"
    env = gym.wrappers.Monitor(env, gym_monitor_path, force=True)
    for _ in range(1000):
        test(agent, env, learned_policy)
    env.close()



Episode#:0 reward:-200.0 best_reward:-200.0 eps:0.999949749999993
Episode#:1 reward:-200.0 best_reward:-200.0 eps:0.999899499999986
Episode#:2 reward:-200.0 best_reward:-200.0 eps:0.9998492499999789
Episode#:3 reward:-200.0 best_reward:-200.0 eps:0.9997989999999719
Episode#:4 reward:-200.0 best_reward:-200.0 eps:0.9997487499999649
Episode#:5 reward:-200.0 best_reward:-200.0 eps:0.9996984999999579
Episode#:6 reward:-200.0 best_reward:-200.0 eps:0.9996482499999508
Episode#:7 reward:-200.0 best_reward:-200.0 eps:0.9995979999999438
Episode#:8 reward:-200.0 best_reward:-200.0 eps:0.9995477499999368
Episode#:9 reward:-200.0 best_reward:-200.0 eps:0.9994974999999298
Episode#:10 reward:-200.0 best_reward:-200.0 eps:0.9994472499999227
Episode#:11 reward:-200.0 best_reward:-200.0 eps:0.9993969999999157
Episode#:12 reward:-200.0 best_reward:-200.0 eps:0.9993467499999087
Episode#:13 reward:-200.0 best_reward:-200.0 eps:0.9992964999999017
Episode#:14 reward:-200.0 best_reward:-200.0 eps:0.999246249

Episode#:126 reward:-200.0 best_reward:-200.0 eps:0.993618249999108
Episode#:127 reward:-200.0 best_reward:-200.0 eps:0.993567999999101
Episode#:128 reward:-200.0 best_reward:-200.0 eps:0.9935177499990939
Episode#:129 reward:-200.0 best_reward:-200.0 eps:0.9934674999990869
Episode#:130 reward:-200.0 best_reward:-200.0 eps:0.9934172499990799
Episode#:131 reward:-200.0 best_reward:-200.0 eps:0.9933669999990729
Episode#:132 reward:-200.0 best_reward:-200.0 eps:0.9933167499990658
Episode#:133 reward:-200.0 best_reward:-200.0 eps:0.9932664999990588
Episode#:134 reward:-200.0 best_reward:-200.0 eps:0.9932162499990518
Episode#:135 reward:-200.0 best_reward:-200.0 eps:0.9931659999990448
Episode#:136 reward:-200.0 best_reward:-200.0 eps:0.9931157499990377
Episode#:137 reward:-200.0 best_reward:-200.0 eps:0.9930654999990307
Episode#:138 reward:-200.0 best_reward:-200.0 eps:0.9930152499990237
Episode#:139 reward:-200.0 best_reward:-200.0 eps:0.9929649999990167
Episode#:140 reward:-200.0 best_rewa

Episode#:250 reward:-200.0 best_reward:-200.0 eps:0.987387249998237
Episode#:251 reward:-200.0 best_reward:-200.0 eps:0.98733699999823
Episode#:252 reward:-200.0 best_reward:-200.0 eps:0.987286749998223
Episode#:253 reward:-200.0 best_reward:-200.0 eps:0.9872364999982159
Episode#:254 reward:-200.0 best_reward:-200.0 eps:0.9871862499982089
Episode#:255 reward:-200.0 best_reward:-200.0 eps:0.9871359999982019
Episode#:256 reward:-200.0 best_reward:-200.0 eps:0.9870857499981949
Episode#:257 reward:-200.0 best_reward:-200.0 eps:0.9870354999981878
Episode#:258 reward:-200.0 best_reward:-200.0 eps:0.9869852499981808
Episode#:259 reward:-200.0 best_reward:-200.0 eps:0.9869349999981738
Episode#:260 reward:-200.0 best_reward:-200.0 eps:0.9868847499981668
Episode#:261 reward:-200.0 best_reward:-200.0 eps:0.9868344999981598
Episode#:262 reward:-200.0 best_reward:-200.0 eps:0.9867842499981527
Episode#:263 reward:-200.0 best_reward:-200.0 eps:0.9867339999981457
Episode#:264 reward:-200.0 best_reward

Episode#:374 reward:-200.0 best_reward:-200.0 eps:0.9811562499973661
Episode#:375 reward:-200.0 best_reward:-200.0 eps:0.981105999997359
Episode#:376 reward:-200.0 best_reward:-200.0 eps:0.981055749997352
Episode#:377 reward:-200.0 best_reward:-200.0 eps:0.981005499997345
Episode#:378 reward:-200.0 best_reward:-200.0 eps:0.980955249997338
Episode#:379 reward:-200.0 best_reward:-200.0 eps:0.9809049999973309
Episode#:380 reward:-200.0 best_reward:-200.0 eps:0.9808547499973239
Episode#:381 reward:-200.0 best_reward:-200.0 eps:0.9808044999973169
Episode#:382 reward:-200.0 best_reward:-200.0 eps:0.9807542499973099
Episode#:383 reward:-200.0 best_reward:-200.0 eps:0.9807039999973028
Episode#:384 reward:-200.0 best_reward:-200.0 eps:0.9806537499972958
Episode#:385 reward:-200.0 best_reward:-200.0 eps:0.9806034999972888
Episode#:386 reward:-200.0 best_reward:-200.0 eps:0.9805532499972818
Episode#:387 reward:-200.0 best_reward:-200.0 eps:0.9805029999972747
Episode#:388 reward:-200.0 best_reward

Episode#:495 reward:-200.0 best_reward:-200.0 eps:0.9750759999965162
Episode#:496 reward:-200.0 best_reward:-200.0 eps:0.9750257499965092
Episode#:497 reward:-200.0 best_reward:-200.0 eps:0.9749754999965021
Episode#:498 reward:-200.0 best_reward:-200.0 eps:0.9749252499964951
Episode#:499 reward:-200.0 best_reward:-200.0 eps:0.9748749999964881
Episode#:500 reward:-200.0 best_reward:-200.0 eps:0.974824749996481
Episode#:501 reward:-200.0 best_reward:-200.0 eps:0.974774499996474
Episode#:502 reward:-200.0 best_reward:-200.0 eps:0.974724249996467
Episode#:503 reward:-200.0 best_reward:-200.0 eps:0.97467399999646
Episode#:504 reward:-200.0 best_reward:-200.0 eps:0.974623749996453
Episode#:505 reward:-200.0 best_reward:-200.0 eps:0.9745734999964459
Episode#:506 reward:-200.0 best_reward:-200.0 eps:0.9745232499964389
Episode#:507 reward:-200.0 best_reward:-200.0 eps:0.9744729999964319
Episode#:508 reward:-200.0 best_reward:-200.0 eps:0.9744227499964249
Episode#:509 reward:-200.0 best_reward:-

...

Episode#:49516 reward:-200.0 best_reward:-200.0 eps:0.0049999999486979654
Episode#:49517 reward:-200.0 best_reward:-200.0 eps:0.0049999999486979654
Episode#:49518 reward:-200.0 best_reward:-200.0 eps:0.0049999999486979654
Episode#:49519 reward:-200.0 best_reward:-200.0 eps:0.0049999999486979654
Episode#:49520 reward:-200.0 best_reward:-200.0 eps:0.0049999999486979654
Episode#:49521 reward:-200.0 best_reward:-200.0 eps:0.0049999999486979654
Episode#:49522 reward:-200.0 best_reward:-200.0 eps:0.0049999999486979654
Episode#:49523 reward:-200.0 best_reward:-200.0 eps:0.0049999999486979654
Episode#:49524 reward:-200.0 best_reward:-200.0 eps:0.0049999999486979654
Episode#:49525 reward:-200.0 best_reward:-200.0 eps:0.0049999999486979654
Episode#:49526 reward:-200.0 best_reward:-200.0 eps:0.0049999999486979654
Episode#:49527 reward:-200.0 best_reward:-200.0 eps:0.0049999999486979654
Episode#:49528 reward:-200.0 best_reward:-200.0 eps:0.0049999999486979654
Episode#:49529 reward:-200.0 best_rewa

Episode#:49630 reward:-200.0 best_reward:-200.0 eps:0.0049999999486979654
Episode#:49631 reward:-200.0 best_reward:-200.0 eps:0.0049999999486979654
Episode#:49632 reward:-200.0 best_reward:-200.0 eps:0.0049999999486979654
Episode#:49633 reward:-200.0 best_reward:-200.0 eps:0.0049999999486979654
Episode#:49634 reward:-200.0 best_reward:-200.0 eps:0.0049999999486979654
Episode#:49635 reward:-200.0 best_reward:-200.0 eps:0.0049999999486979654
Episode#:49636 reward:-200.0 best_reward:-200.0 eps:0.0049999999486979654
Episode#:49637 reward:-200.0 best_reward:-200.0 eps:0.0049999999486979654
Episode#:49638 reward:-200.0 best_reward:-200.0 eps:0.0049999999486979654
Episode#:49639 reward:-200.0 best_reward:-200.0 eps:0.0049999999486979654
Episode#:49640 reward:-200.0 best_reward:-200.0 eps:0.0049999999486979654
Episode#:49641 reward:-200.0 best_reward:-200.0 eps:0.0049999999486979654
Episode#:49642 reward:-200.0 best_reward:-200.0 eps:0.0049999999486979654
Episode#:49643 reward:-200.0 best_rewa

Episode#:49752 reward:-200.0 best_reward:-200.0 eps:0.0049999999486979654
Episode#:49753 reward:-200.0 best_reward:-200.0 eps:0.0049999999486979654
Episode#:49754 reward:-200.0 best_reward:-200.0 eps:0.0049999999486979654
Episode#:49755 reward:-200.0 best_reward:-200.0 eps:0.0049999999486979654
Episode#:49756 reward:-200.0 best_reward:-200.0 eps:0.0049999999486979654
Episode#:49757 reward:-200.0 best_reward:-200.0 eps:0.0049999999486979654
Episode#:49758 reward:-200.0 best_reward:-200.0 eps:0.0049999999486979654
Episode#:49759 reward:-200.0 best_reward:-200.0 eps:0.0049999999486979654
Episode#:49760 reward:-200.0 best_reward:-200.0 eps:0.0049999999486979654
Episode#:49761 reward:-200.0 best_reward:-200.0 eps:0.0049999999486979654
Episode#:49762 reward:-200.0 best_reward:-200.0 eps:0.0049999999486979654
Episode#:49763 reward:-200.0 best_reward:-200.0 eps:0.0049999999486979654
Episode#:49764 reward:-200.0 best_reward:-200.0 eps:0.0049999999486979654
Episode#:49765 reward:-200.0 best_rewa

Episode#:49865 reward:-200.0 best_reward:-200.0 eps:0.0049999999486979654
Episode#:49866 reward:-200.0 best_reward:-200.0 eps:0.0049999999486979654
Episode#:49867 reward:-200.0 best_reward:-200.0 eps:0.0049999999486979654
Episode#:49868 reward:-200.0 best_reward:-200.0 eps:0.0049999999486979654
Episode#:49869 reward:-200.0 best_reward:-200.0 eps:0.0049999999486979654
Episode#:49870 reward:-200.0 best_reward:-200.0 eps:0.0049999999486979654
Episode#:49871 reward:-200.0 best_reward:-200.0 eps:0.0049999999486979654
Episode#:49872 reward:-200.0 best_reward:-200.0 eps:0.0049999999486979654
Episode#:49873 reward:-200.0 best_reward:-200.0 eps:0.0049999999486979654
Episode#:49874 reward:-200.0 best_reward:-200.0 eps:0.0049999999486979654
Episode#:49875 reward:-200.0 best_reward:-200.0 eps:0.0049999999486979654
Episode#:49876 reward:-200.0 best_reward:-200.0 eps:0.0049999999486979654
Episode#:49877 reward:-200.0 best_reward:-200.0 eps:0.0049999999486979654
Episode#:49878 reward:-200.0 best_rewa

Episode#:49977 reward:-200.0 best_reward:-200.0 eps:0.0049999999486979654
Episode#:49978 reward:-200.0 best_reward:-200.0 eps:0.0049999999486979654
Episode#:49979 reward:-200.0 best_reward:-200.0 eps:0.0049999999486979654
Episode#:49980 reward:-200.0 best_reward:-200.0 eps:0.0049999999486979654
Episode#:49981 reward:-200.0 best_reward:-200.0 eps:0.0049999999486979654
Episode#:49982 reward:-200.0 best_reward:-200.0 eps:0.0049999999486979654
Episode#:49983 reward:-200.0 best_reward:-200.0 eps:0.0049999999486979654
Episode#:49984 reward:-200.0 best_reward:-200.0 eps:0.0049999999486979654
Episode#:49985 reward:-200.0 best_reward:-200.0 eps:0.0049999999486979654
Episode#:49986 reward:-200.0 best_reward:-200.0 eps:0.0049999999486979654
Episode#:49987 reward:-200.0 best_reward:-200.0 eps:0.0049999999486979654
Episode#:49988 reward:-200.0 best_reward:-200.0 eps:0.0049999999486979654
Episode#:49989 reward:-200.0 best_reward:-200.0 eps:0.0049999999486979654
Episode#:49990 reward:-200.0 best_rewa